In [29]:
import pickle
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import re
import urllib.request
from konlpy.tag import Okt
from tqdm import tqdm
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences

In [30]:
urllib.request.urlretrieve("https://raw.githubusercontent.com/e9t/nsmc/master/ratings_train.txt", filename="ratings_train.txt")
urllib.request.urlretrieve("https://raw.githubusercontent.com/e9t/nsmc/master/ratings_test.txt", filename="ratings_test.txt")

('ratings_test.txt', <http.client.HTTPMessage at 0x218c055e750>)

In [31]:
train_data = pd.read_table('ratings_train.txt')
test_data = pd.read_table('ratings_test.txt')

In [32]:
# 결측값 제거 (document 열에서 NaN 값이 있는 경우 삭제)
train_data = train_data.dropna(subset=['document'])

# 텍스트가 문자열인지 확인 후 길이 계산
train_data['document'] = train_data['document'].astype(str)  # 모든 document를 문자열로 변환

# 리뷰 텍스트의 길이 계산
train_data['length'] = train_data['document'].apply(len)

# 최솟값, 최댓값, 평균 계산
min_length = train_data['length'].min()
max_length = train_data['length'].max()
avg_length = train_data['length'].mean()

print(f"최솟값: {min_length}")
print(f"최댓값: {max_length}")
print(f"평균값: {avg_length:.2f}")

최솟값: 1
최댓값: 146
평균값: 35.20


In [33]:
import sentencepiece as spm

spm.SentencePieceTrainer.train(input='ratings_train.txt', model_prefix='naver_spm', vocab_size=8000)

In [34]:
s = spm.SentencePieceProcessor(model_file='naver_spm.model')
# Ensure all entries are strings and handle missing values
train_data['document'] = train_data['document'].astype(str).fillna('')
test_data['document'] = test_data['document'].astype(str).fillna('')

# Tokenize the data
train_data['tokenized'] = train_data['document'].apply(lambda x: s.encode_as_ids(x))
test_data['tokenized'] = test_data['document'].apply(lambda x: s.encode_as_ids(x))

In [35]:
import pandas as pd
import sentencepiece as spm
from sklearn.model_selection import train_test_split
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Embedding, LSTM, Dense

max_len = 40
X = pad_sequences(train_data['tokenized'], maxlen=max_len, padding='pre')

# 7. 레이블 준비
y = to_categorical(train_data['label'])
# 8. 데이터 분할 (훈련셋과 검증셋)
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, random_state=42)

In [11]:
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Embedding, Flatten, Conv1D, MaxPooling1D, GlobalMaxPooling1D, LSTM
from tensorflow.keras.preprocessing.sequence import pad_sequences

vocab_size = 10000  # 어휘 사전의 크기
word_vector_dim = 32   # 임베딩 벡터의 차원

# 1. 모델 구성
model1 = tf.keras.Sequential()
model1.add(tf.keras.layers.Embedding(vocab_size, word_vector_dim, input_shape=(None,)))

# 첫 번째 Conv1D 레이어
model1.add(tf.keras.layers.Conv1D(16, 3, activation='relu'))  # 커널 크기 3
model1.add(tf.keras.layers.MaxPooling1D(2))  # 풀링 크기 2

# 두 번째 Conv1D 레이어
model1.add(tf.keras.layers.Conv1D(16, 3, activation='relu'))  # 커널 크기 3
model1.add(tf.keras.layers.GlobalMaxPooling1D())

# Dense 레이어
model1.add(tf.keras.layers.Dense(8, activation='relu'))
model1.add(tf.keras.layers.Dense(1, activation='sigmoid'))  # 이진 분류를 위한 출력층

# 2. 모델 컴파일
model1.compile(optimizer='adam',
              loss='binary_crossentropy',
              metrics=['accuracy'])

y_train_binary = np.argmax(y_train, axis=1)
y_val_binary = np.argmax(y_val, axis=1)

# 모델 요약 정보 출력
model1.summary()

c:\Users\jinmi\AppData\Local\Programs\Python\Python311\Lib\site-packages\keras\src\layers\core\embedding.py:93: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


Model: "sequential_1"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ embedding_1 (Embedding)         │ (None, None, 32)       │       320,000 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv1d_2 (Conv1D)               │ (None, None, 16)       │         1,552 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling1d_1 (MaxPooling1D)  │ (None, None, 16)       │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv1d_3 (Conv1D)               │ (None, None, 16)       │           784 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ global_max_pooling1d_1          │ (None, 16)             │             0 │
│ (GlobalMaxPooling1D)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_2 (Dense)                 │ (None, 8)              │           136 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_3 (Dense)                 │ (None, 1)              │             9 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 322,481 (1.23 MB)

 Trainable params: 322,481 (1.23 MB)

 Non-trainable params: 0 (0.00 B)

In [12]:
epochs= 5  # 몇 epoch를 훈련하면 좋을지 결과를 보면서 바꾸어 봅시다.

history = model1.fit(X_train,
                    y_train_binary,  # 이진 레이블을 사용
                    epochs=epochs,
                    batch_size=512,
                    validation_data=(X_val, y_val_binary),  # 이진 레이블을 사용
                    verbose=1)

Epoch 1/5
235/235 ━━━━━━━━━━━━━━━━━━━━ 11s 22ms/step - accuracy: 0.6047 - loss: 0.6441 - val_accuracy: 0.8342 - val_loss: 0.3790
Epoch 2/5
235/235 ━━━━━━━━━━━━━━━━━━━━ 5s 20ms/step - accuracy: 0.8494 - loss: 0.3475 - val_accuracy: 0.8495 - val_loss: 0.3419
Epoch 3/5
235/235 ━━━━━━━━━━━━━━━━━━━━ 5s 19ms/step - accuracy: 0.8766 - loss: 0.2959 - val_accuracy: 0.8532 - val_loss: 0.3372
Epoch 4/5
235/235 ━━━━━━━━━━━━━━━━━━━━ 7s 29ms/step - accuracy: 0.8932 - loss: 0.2651 - val_accuracy: 0.8520 - val_loss: 0.3451
Epoch 5/5
235/235 ━━━━━━━━━━━━━━━━━━━━ 16s 52ms/step - accuracy: 0.9097 - loss: 0.2297 - val_accuracy: 0.8490 - val_loss: 0.3604


In [14]:
# 1. 테스트 데이터 로드
test_data = pd.read_table('ratings_test.txt')

# 2. 결측값 제거
test_data = test_data.dropna(subset=['document','label'])

# 3. 레이블 준비(감정 분석 레이블)
y_test = test_data['label'].values

# 이미 학습된 sentencepiece 모델을 로드
import sentencepiece as spm
sp = spm.SentencePieceProcessor()
sp.load('naver_spm.model')

# 리뷰를 토큰화하여 ID로 변환
x_test = test_data['document'].apply(lambda x: sp.encode_as_ids(str(x)))

# 5. 패딩 처리 (최대 길이 80으로 설정)
max_len = 80
x_test_padded = pad_sequences(x_test, maxlen=max_len, padding='pre')

# 이제 x_test_padded와 y_test를 사용하여 모델을 평가할 수 있습니다.
results = model1.evaluate(x_test_padded, y_test, verbose=2)
print(f"테스트 데이터에서의 손실: {results[0]}, 정확도: {results[1]}")

1563/1563 - 10s - 6ms/step - accuracy: 0.8487 - loss: 0.3642
테스트 데이터에서의 손실: 0.3642037808895111, 정확도: 0.8486708998680115


# 모델2 구성(Global MaxPooling only)

In [15]:
import tensorflow as tf
vocab_size =10000
word_vector_dim = 32

model2 = tf.keras.Sequential()
model2.add(tf.keras.layers.Embedding(vocab_size, word_vector_dim, input_shape=(None,)))
model2.add(tf.keras.layers.GlobalMaxPooling1D())
model2.add(tf.keras.layers.Dense(8, activation='relu'))
model2.add(tf.keras.layers.Dense(1, activation='sigmoid'))  # 최종 출력은 긍정/부정을 나타내는 1dim 입니다.

model2.summary()

c:\Users\jinmi\AppData\Local\Programs\Python\Python311\Lib\site-packages\keras\src\layers\core\embedding.py:93: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


Model: "sequential_2"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ embedding_2 (Embedding)         │ (None, None, 32)       │       320,000 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ global_max_pooling1d_2          │ (None, 32)             │             0 │
│ (GlobalMaxPooling1D)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_4 (Dense)                 │ (None, 8)              │           264 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_5 (Dense)                 │ (None, 1)              │             9 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 320,273 (1.22 MB)

 Trainable params: 320,273 (1.22 MB)

 Non-trainable params: 0 (0.00 B)

In [16]:
model2.compile(optimizer='adam',
               loss='binary_crossentropy',
               metrics=['accuracy'])

y_train_binary = np.argmax(y_train, axis=1)
y_val_binary = np.argmax(y_val, axis=1)
epoch = 5
history2 = model2.fit(X_train,
                    y_train_binary,  # 이진 레이블을 사용
                    epochs=epoch,
                    batch_size=512,
                    validation_data=(X_val, y_val_binary),  # 이진 레이블을 사용
                    verbose=1)

Epoch 1/5
235/235 ━━━━━━━━━━━━━━━━━━━━ 7s 18ms/step - accuracy: 0.6000 - loss: 0.6563 - val_accuracy: 0.8339 - val_loss: 0.4054
Epoch 2/5
235/235 ━━━━━━━━━━━━━━━━━━━━ 4s 16ms/step - accuracy: 0.8526 - loss: 0.3632 - val_accuracy: 0.8500 - val_loss: 0.3447
Epoch 3/5
235/235 ━━━━━━━━━━━━━━━━━━━━ 4s 15ms/step - accuracy: 0.8761 - loss: 0.2987 - val_accuracy: 0.8517 - val_loss: 0.3403
Epoch 4/5
235/235 ━━━━━━━━━━━━━━━━━━━━ 3s 14ms/step - accuracy: 0.8885 - loss: 0.2695 - val_accuracy: 0.8508 - val_loss: 0.3434
Epoch 5/5
235/235 ━━━━━━━━━━━━━━━━━━━━ 4s 16ms/step - accuracy: 0.8981 - loss: 0.2491 - val_accuracy: 0.8519 - val_loss: 0.3498


In [17]:
# 1. 테스트 데이터 로드
test_data = pd.read_table('ratings_test.txt')

# 2. 결측값 제거
test_data = test_data.dropna(subset=['document','label'])

# 3. 레이블 준비(감정 분석 레이블)
y_test = test_data['label'].values

# 이미 학습된 sentencepiece 모델을 로드
import sentencepiece as spm
sp = spm.SentencePieceProcessor()
sp.load('naver_spm.model')

# 리뷰를 토큰화하여 ID로 변환
x_test = test_data['document'].apply(lambda x: sp.encode_as_ids(str(x)))

# 5. 패딩 처리 (최대 길이 80으로 설정)
max_len = 80
x_test_padded = pad_sequences(x_test, maxlen=max_len, padding='pre')

# 이제 x_test_padded와 y_test를 사용하여 모델을 평가할 수 있습니다.
results = model2.evaluate(x_test_padded, y_test, verbose=2)
print(f"테스트 데이터에서의 손실: {results[0]}, 정확도: {results[1]}")

1563/1563 - 3s - 2ms/step - accuracy: 0.8481 - loss: 0.3594
테스트 데이터에서의 손실: 0.3594205975532532, 정확도: 0.8481109142303467


# 모델3. LSTM

In [18]:
vocab_size = 10000
word_vector_dim = 32

model3 = tf.keras.Sequential()
model3.add(tf.keras.layers.Embedding(vocab_size, word_vector_dim, input_shape=(None,)))
model3.add(tf.keras.layers.LSTM(16))
model3.add(tf.keras.layers.Dense(16, activation='relu'))
model3.add(tf.keras.layers.Dense(1, activation='sigmoid'))  # 최종 출력은 긍정/부정을 나타내는 1dim 입니다.

c:\Users\jinmi\AppData\Local\Programs\Python\Python311\Lib\site-packages\keras\src\layers\core\embedding.py:93: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


In [19]:
model3.compile(optimizer='adam',
               loss='binary_crossentropy',
               metrics=['accuracy'])

y_train_binary = np.argmax(y_train, axis=1)
y_val_binary = np.argmax(y_val, axis=1)
epochs=5

history3 = model3.fit(X_train,
                    y_train_binary,  # 이진 레이블을 사용
                    epochs=epoch,
                    batch_size=512,
                    validation_data=(X_val, y_val_binary),  # 이진 레이블을 사용
                    verbose=1)

Epoch 1/5
235/235 ━━━━━━━━━━━━━━━━━━━━ 29s 81ms/step - accuracy: 0.7082 - loss: 0.5727 - val_accuracy: 0.8485 - val_loss: 0.3508
Epoch 2/5
235/235 ━━━━━━━━━━━━━━━━━━━━ 16s 66ms/step - accuracy: 0.8635 - loss: 0.3251 - val_accuracy: 0.8504 - val_loss: 0.3416
Epoch 3/5
235/235 ━━━━━━━━━━━━━━━━━━━━ 15s 64ms/step - accuracy: 0.8719 - loss: 0.3049 - val_accuracy: 0.8489 - val_loss: 0.3422
Epoch 4/5
235/235 ━━━━━━━━━━━━━━━━━━━━ 16s 68ms/step - accuracy: 0.8798 - loss: 0.2905 - val_accuracy: 0.8521 - val_loss: 0.3396
Epoch 5/5
235/235 ━━━━━━━━━━━━━━━━━━━━ 17s 71ms/step - accuracy: 0.8868 - loss: 0.2761 - val_accuracy: 0.8517 - val_loss: 0.3421


In [22]:
# 1. 테스트 데이터 로드
test_data = pd.read_table('ratings_test.txt')

# 2. 결측값 제거
test_data = test_data.dropna(subset=['document','label'])

# 3. 레이블 준비(감정 분석 레이블)
y_test = test_data['label'].values

# 이미 학습된 sentencepiece 모델을 로드
import sentencepiece as spm
sp = spm.SentencePieceProcessor()
sp.load('naver_spm.model')

# 리뷰를 토큰화하여 ID로 변환
x_test = test_data['document'].apply(lambda x: sp.encode_as_ids(str(x)))

# 5. 패딩 처리 (최대 길이 80으로 설정)
max_len = 80
x_test_padded = pad_sequences(x_test, maxlen=max_len, padding='pre')

# 이제 x_test_padded와 y_test를 사용하여 모델을 평가할 수 있습니다.
results = model3.evaluate(x_test_padded, y_test, verbose=2)
print(f"테스트 데이터에서의 손실: {results[0]}, 정확도: {results[1]}")

1563/1563 - 30s - 19ms/step - accuracy: 0.8476 - loss: 0.3479
테스트 데이터에서의 손실: 0.34787091612815857, 정확도: 0.8476308584213257


# 모델4. (transformer 1개 16차원)

In [23]:
vocab_size = 10001
word_vector_dim = 32

model4 = tf.keras.Sequential()
model4.add(tf.keras.layers.Embedding(vocab_size, word_vector_dim, input_shape=(None,)))
model4.add(tf.keras.layers.LSTM(16))   # 가장 널리 쓰이는 RNN인 LSTM 레이어를 사용하였습니다. 이때 LSTM state 벡터의 차원수는 8로 하였습니다. (변경 가능)
model4.add(tf.keras.layers.Dense(16, activation='relu'))
model4.add(tf.keras.layers.Dense(1, activation='sigmoid'))  # 최종 출력은 긍정/부정을 나타내는 1dim 입니다.
model4.summary()

c:\Users\jinmi\AppData\Local\Programs\Python\Python311\Lib\site-packages\keras\src\layers\core\embedding.py:93: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


Model: "sequential_4"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ embedding_4 (Embedding)         │ (None, None, 32)       │       320,032 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ lstm_1 (LSTM)                   │ (None, 16)             │         3,136 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_8 (Dense)                 │ (None, 16)             │           272 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_9 (Dense)                 │ (None, 1)              │            17 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 323,457 (1.23 MB)

 Trainable params: 323,457 (1.23 MB)

 Non-trainable params: 0 (0.00 B)

In [24]:
model4.compile(optimizer='adam',
               loss='binary_crossentropy',
               metrics=['accuracy'])

epochs = 6

y_train_binary = np.argmax(y_train, axis=1)
y_val_binary = np.argmax(y_val, axis=1)


history4 = model4.fit(X_train,
                    y_train_binary,  # 이진 레이블을 사용
                    epochs=epochs,
                    batch_size=512,
                    validation_data=(X_val, y_val_binary),  # 이진 레이블을 사용
                    verbose=1)

Epoch 1/6
235/235 ━━━━━━━━━━━━━━━━━━━━ 21s 64ms/step - accuracy: 0.6927 - loss: 0.5784 - val_accuracy: 0.8467 - val_loss: 0.3527
Epoch 2/6
235/235 ━━━━━━━━━━━━━━━━━━━━ 14s 60ms/step - accuracy: 0.8639 - loss: 0.3243 - val_accuracy: 0.8527 - val_loss: 0.3390
Epoch 3/6
235/235 ━━━━━━━━━━━━━━━━━━━━ 11s 48ms/step - accuracy: 0.8720 - loss: 0.3056 - val_accuracy: 0.8532 - val_loss: 0.3415
Epoch 4/6
235/235 ━━━━━━━━━━━━━━━━━━━━ 24s 104ms/step - accuracy: 0.8804 - loss: 0.2858 - val_accuracy: 0.8555 - val_loss: 0.3356
Epoch 5/6
235/235 ━━━━━━━━━━━━━━━━━━━━ 45s 121ms/step - accuracy: 0.8879 - loss: 0.2707 - val_accuracy: 0.8555 - val_loss: 0.3443
Epoch 6/6
235/235 ━━━━━━━━━━━━━━━━━━━━ 23s 96ms/step - accuracy: 0.8920 - loss: 0.2593 - val_accuracy: 0.8527 - val_loss: 0.3473


In [25]:
# 1. 테스트 데이터 로드
test_data = pd.read_table('ratings_test.txt')

# 2. 결측값 제거
test_data = test_data.dropna(subset=['document','label'])

# 3. 레이블 준비(감정 분석 레이블)
y_test = test_data['label'].values

# 이미 학습된 sentencepiece 모델을 로드
import sentencepiece as spm
sp = spm.SentencePieceProcessor()
sp.load('naver_spm.model')

# 리뷰를 토큰화하여 ID로 변환
x_test = test_data['document'].apply(lambda x: sp.encode_as_ids(str(x)))

# 5. 패딩 처리 (최대 길이 80으로 설정)
max_len = 80
x_test_padded = pad_sequences(x_test, maxlen=max_len, padding='pre')

# 이제 x_test_padded와 y_test를 사용하여 모델을 평가할 수 있습니다.
results = model4.evaluate(x_test_padded, y_test, verbose=2)
print(f"테스트 데이터에서의 손실: {results[0]}, 정확도: {results[1]}")

1563/1563 - 16s - 10ms/step - accuracy: 0.8490 - loss: 0.3572
테스트 데이터에서의 손실: 0.35723575949668884, 정확도: 0.8489709496498108


# SP_TOKENIZE

In [38]:
"""
def sp_tokenize(sp, corpus, vocab_path):
    tokenized_tensor = []
    word_index = {}
    index_word = {}

    # vocab 파일을 읽을 때 인코딩을 명시적으로 utf-8로 설정
    with open(vocab_path, 'r', encoding='utf-8') as vocab_file:
        for i, line in enumerate(vocab_file):
            token = line.strip().split('\t')[0]
            word_index[token] = i
            index_word[i] = token

    # 문장을 SentencePiece 모델을 통해 토큰화
    for sentence in corpus:
        tokens = sp.encode_as_ids(sentence)
        tokenized_tensor.append(tokens)

    return tokenized_tensor, word_index, index_word
"""

In [45]:
def sp_tokenize(sp, corpus):
    tokenized_tensor = []
    
    for sentence in corpus:
        # 문장을 SentencePiece를 사용해 정수 인덱스로 변환
        tokens = sp.encode_as_ids(sentence)
        tokenized_tensor.append(tokens)

    return tokenized_tensor

In [39]:
"""
import sentencepiece as spm
sp = spm.SentencePieceProcessor()
sp.load('naver_spm.model')

corpus = test_data['document']

tokenized_tensor, word_index, index_word = sp_tokenize(sp, corpus, 'naver_spm.vocab')

print(tokenized_tensor)  # Padded tokenized reviews
print(word_index)        # Word-to-index mapping
print(index_word)        # Index-to-word mapping
"""

[[3078, 333], [3, 3250, 1113, 4101, 3164, 2803, 3776, 3376, 3470, 3768, 3165, 3165, 4652, 4101, 3164, 5253, 3063, 3376, 3470, 5543, 3454], [1573, 38, 101, 418, 65, 123, 3651, 104, 4524, 26, 55, 2306, 730, 77, 261, 3593, 6891], [3144, 16, 6662, 145, 631, 107, 11, 2811, 5746, 65], [31, 1113, 33, 267, 4334, 15, 250, 6106, 147, 3, 1594, 3191, 9, 69, 31, 1113, 37, 1566, 343, 530, 1064, 3086, 88, 197, 376, 233], [3813, 216, 14, 825, 17, 131, 592, 42], [1383, 120], [3314, 657, 3201, 57, 3, 4642, 46, 3548, 1117, 3, 605, 13, 686, 275, 4677, 309, 64, 50, 222, 14, 17, 21, 180, 30, 3, 6068, 39, 312], [1138, 3895, 415, 690, 1040, 42, 3123, 345, 1275, 3, 5216, 962, 23, 518, 257, 5222, 212, 781, 2719, 1165, 943, 257, 256, 70, 5891, 602, 91, 53, 930, 246, 137, 146, 31, 334, 54, 334, 266, 103], [38, 1044, 13, 4187, 3138, 20, 1011, 3099, 1950, 669, 290, 13, 320, 7985, 755, 5727, 17, 489, 838, 5149, 16, 793, 56, 9], [1046, 68, 170, 3958, 33, 745, 5074, 3507, 3156, 797, 7669, 223], [299, 930, 2616, 42, 13

In [46]:
tokenized_train = sp_tokenize(sp, corpus_train)
tokenized_test = sp_tokenize(sp, corpus_test)

In [47]:
X = pad_sequences(tokenized_train, maxlen=max_len, padding='pre')
X_1 = pad_sequences(tokenized_test, maxlen=max_len, padding='pre')
X_test, y_test = train_test_split(X_1,)
y = to_categorical(train_data['label'])
# 8. 데이터 분할(훈련셋과 검증셋)
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, random_state=42)

#모델 1 구성 (Conv1D + MaxPooling)

In [54]:
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Embedding, Flatten, Conv1D, MaxPooling1D, GlobalMaxPooling1D, LSTM
from tensorflow.keras.preprocessing.sequence import pad_sequences

vocab_size = 10000  # 어휘 사전의 크기
word_vector_dim = 32   # 임베딩 벡터의 차원

# 1. 모델 구성
model1 = tf.keras.Sequential()
model1.add(tf.keras.layers.Embedding(vocab_size, word_vector_dim, input_shape=(None,)))

# 첫 번째 Conv1D 레이어
model1.add(tf.keras.layers.Conv1D(16, 3, activation='relu'))  # 커널 크기 3
model1.add(tf.keras.layers.MaxPooling1D(2))  # 풀링 크기 2

# 두 번째 Conv1D 레이어
model1.add(tf.keras.layers.Conv1D(16, 3, activation='relu'))  # 커널 크기 3
model1.add(tf.keras.layers.GlobalMaxPooling1D())

# Dense 레이어
model1.add(tf.keras.layers.Dense(8, activation='relu'))
model1.add(tf.keras.layers.Dense(1, activation='sigmoid'))  # 이진 분류를 위한 출력층


c:\Users\jinmi\AppData\Local\Programs\Python\Python311\Lib\site-packages\keras\src\layers\core\embedding.py:93: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


In [56]:
# 2. 모델 컴파일
model1.compile(optimizer='adam',
              loss='binary_crossentropy',
              metrics=['accuracy'])

y_train_binary = np.argmax(y_train, axis=1)
y_val_binary = np.argmax(y_val, axis=1)

# 모델 요약 정보 출력
model1.summary()

Model: "sequential_5"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ embedding_5 (Embedding)         │ (None, None, 32)       │       320,000 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv1d_4 (Conv1D)               │ (None, None, 16)       │         1,552 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling1d_2 (MaxPooling1D)  │ (None, None, 16)       │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv1d_5 (Conv1D)               │ (None, None, 16)       │           784 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ global_max_pooling1d_3          │ (None, 16)             │             0 │
│ (GlobalMaxPooling1D)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_10 (Dense)                │ (None, 8)              │           136 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_11 (Dense)                │ (None, 1)              │             9 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 322,481 (1.23 MB)

 Trainable params: 322,481 (1.23 MB)

 Non-trainable params: 0 (0.00 B)

In [57]:
epochs= 5  # 몇 epoch를 훈련하면 좋을지 결과를 보면서 바꾸어 봅시다.

history = model1.fit(X_train,
                    y_train_binary,  # 이진 레이블을 사용
                    epochs=epochs,
                    batch_size=512,
                    validation_data=(X_val, y_val_binary),  # 이진 레이블을 사용
                    verbose=1)

Epoch 1/5
235/235 ━━━━━━━━━━━━━━━━━━━━ 29s 104ms/step - accuracy: 0.6344 - loss: 0.6156 - val_accuracy: 0.8424 - val_loss: 0.3586
Epoch 2/5
235/235 ━━━━━━━━━━━━━━━━━━━━ 13s 49ms/step - accuracy: 0.8598 - loss: 0.3271 - val_accuracy: 0.8493 - val_loss: 0.3405
Epoch 3/5
235/235 ━━━━━━━━━━━━━━━━━━━━ 14s 59ms/step - accuracy: 0.8842 - loss: 0.2837 - val_accuracy: 0.8495 - val_loss: 0.3439
Epoch 4/5
235/235 ━━━━━━━━━━━━━━━━━━━━ 14s 56ms/step - accuracy: 0.9008 - loss: 0.2487 - val_accuracy: 0.8469 - val_loss: 0.3485
Epoch 5/5
235/235 ━━━━━━━━━━━━━━━━━━━━ 13s 51ms/step - accuracy: 0.9190 - loss: 0.2125 - val_accuracy: 0.8437 - val_loss: 0.3710
